<a href="https://colab.research.google.com/github/italolima04/data-science-covid-19/blob/master/HeatMap-Cidades-BR-Covid-19/Heat_Map_Covid_BR.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [186]:
#Importando Bibliotecas e Módulos.
import pandas as pd
import numpy as np

import folium
from folium import plugins

In [187]:
#Importando os dados e Criando Data Frame a partir destes.
df = pd.read_csv('covid-dados-br.csv')
#Visualizando às 5 primeiras linhas.
df.head()

epidemiological_week        date  ...  is_last is_repeated
0                    26  2020-06-25  ...     True       False
1                    26  2020-06-25  ...     True       False
2                    26  2020-06-25  ...     True       False
3                    26  2020-06-25  ...     True       False
4                    26  2020-06-25  ...     True       False

[5 rows x 16 columns]

In [188]:
#Criando Data Frame Auxiliar.
cidades = pd.read_csv('https://raw.githubusercontent.com/sandeco/CanalSandeco/master/covid-19/cidades_brasil.csv')
cidades.head()

codigo_ibge                 nome  latitude  longitude  capital  codigo_uf
0      5200050      Abadia de Goiás -16.75730   -49.4412        0         52
1      3100104  Abadia dos Dourados -18.48310   -47.3916        0         31
2      5200100            Abadiânia -16.19700   -48.7057        0         52
3      3100203               Abaeté -19.15510   -45.4444        0         31
4      1500107           Abaetetuba  -1.72183   -48.8788        0         15

In [189]:
#Tornando o código do IBGE como Index para o Data Frame. Espécie de ID.
cidades = cidades.set_index('codigo_ibge')

In [190]:
#Filtrando os dados. Iremos trabalhar apenas com as cidades.
cities = df.loc[df.place_type == 'city', :]
cities.head()

epidemiological_week        date  ...  is_last is_repeated
0                    26  2020-06-25  ...     True       False
1                    26  2020-06-25  ...     True       False
2                    26  2020-06-25  ...     True       False
3                    26  2020-06-25  ...     True       False
4                    26  2020-06-25  ...     True       False

[5 rows x 16 columns]

In [191]:
#Verificando se a filtragem foi bem sucedida.
cities.place_type.unique()

array(['city'], dtype=object)

In [192]:
#Fazendo um join entre doid Data Frames, (unindo-os) a partir do código do IBGE para cada cidade.
cities = cities.join(cidades, on='city_ibge_code')

In [193]:
#Visualizando os dados.
cities.head()

epidemiological_week        date  ...  capital codigo_uf
0                    26  2020-06-25  ...      0.0      12.0
1                    26  2020-06-25  ...      0.0      12.0
2                    26  2020-06-25  ...      0.0      12.0
3                    26  2020-06-25  ...      0.0      12.0
4                    26  2020-06-25  ...      0.0      12.0

[5 rows x 21 columns]

In [194]:
#Filtrando somente as colunas de interesse para o estudo, a partir das últimas atualizações para cada cidade.
geo_last = cities.loc[cities.is_last == True, ['city', 'latitude', 'longitude', 'state', 'last_available_confirmed', 'last_available_deaths']]
geo_last.head()

city  latitude  ...  last_available_confirmed last_available_deaths
0    Acrelândia  -9.82581  ...                       185                     3
1  Assis Brasil -10.92980  ...                       147                     5
2     Brasiléia -10.99500  ...                       287                     6
3        Bujari  -9.81528  ...                       151                     3
4      Capixaba -10.56600  ...                       128                     5

[5 rows x 6 columns]

In [195]:
#Quantidade de cidades com casos confirmados.
len(geo_last['city'])

5029

In [196]:
#Quantidade de Casos Confirmados.
geo_last['last_available_confirmed'].sum()

1218066

In [197]:
#Quantidade de Óbitos Registrados.
geo_last['last_available_deaths'].sum()

54749

In [198]:
#Verificando os estados com Casos Confirmados.
geo_last['state'].unique()

array(['AC', 'AL', 'AM', 'AP', 'ES', 'GO', 'MA', 'MG', 'MT', 'PA', 'PE',
       'PI', 'PR', 'RJ', 'RS', 'SC', 'SP', 'BA', 'CE', 'DF', 'MS', 'SE',
       'TO', 'RN', 'RO', 'RR', 'PB'], dtype=object)

In [199]:
#Confirmando a quantidade de estados. Todos os estados do Brasil registram dados da COVID-19.
len(geo_last['state'].unique())

27

In [200]:
#Criando novo Data Frame.
coordenadas = geo_last[['latitude', 'longitude', 'last_available_confirmed']]
coordenadas.head()

latitude  longitude  last_available_confirmed
0  -9.82581   -66.8972                       185
1 -10.92980   -69.5738                       147
2 -10.99500   -68.7497                       287
3  -9.81528   -67.9550                       151
4 -10.56600   -67.6860                       128

In [201]:
#Verificando a estrutura do Data Frame.
coordenadas.shape

(5029, 3)

In [202]:
#Verificando a presença de dados nulos.
coordenadas.isna().sum()

latitude                    17
longitude                   17
last_available_confirmed     0
dtype: int64

In [203]:
#Removendo valores NaN.
coordenadas = coordenadas.dropna()

In [204]:
#Verificando a nova estrutura do Data Frame.
coordenadas.shape

(5012, 3)

In [205]:
coordenadas.isna().sum()

latitude                    0
longitude                   0
last_available_confirmed    0
dtype: int64

In [206]:
#Criando base do Mapa, configurando os parâmetros de exibição inicial.
baseMap = folium.Map(
    width="100%",
    height="100%",
    location=[-15.788497, -47.879873],
    zoom_start=4,
)

In [207]:
baseMap

In [208]:
#Transformando o Data Frame em um Array de Valores.
coordenadas = coordenadas.values

In [209]:
#Criando o HeatMap a partir do Mapa Base. 
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [210]:
#Visualizando o Mapa de Calor.
baseMap

**É necessário remover os dados NaN do Data Frame que será utilizado para gerar o HeatMap.**

In [211]:
geo_last.shape

(5029, 6)

In [212]:
geo_last.isna().sum()

city                         0
latitude                    17
longitude                   17
state                        0
last_available_confirmed     0
last_available_deaths        0
dtype: int64

In [213]:
geo_last = geo_last.dropna()

In [214]:
geo_last.shape

(5012, 6)

In [215]:
#Configurando o Mapa de Calor a partir dos dados de Casos Confirmados. Configurando parâmetros de exibição, como uma descrição da situação de cada cidade e o marcador o mapa.
for i in range(0, len(geo_last)):
  folium.Circle(
      location = [geo_last.iloc[i]['latitude'], geo_last.iloc[i]['longitude']],
      color = "#00FF69",
      fill = "#00A1B3",
      tooltip = "<li> <bold> Cidade: " + str(geo_last.iloc[i]['city']) + 
                "<li> <bold> Estado: " + str(geo_last.iloc[i]['state']) + 
                "<li> <bold> Confirmados: " + str(geo_last.iloc[i]['last_available_confirmed']) + 
                "<li> <bold> Óbitos: " + str(geo_last.iloc[i]['last_available_deaths']),   
      radius = (geo_last.iloc[i]['last_available_confirmed'] ** 1.1)          
  ).add_to(baseMap)

In [216]:
 #Visualizando Heat Map
 baseMap

In [217]:
#Exportando Arquivo em Formato HTML.
baseMap.save('heatMap-cidades.html')